## Decision Tree
This example demostrates how to train a decision tree model and visualize the tree structure. It also shows how to perform hyper parameter tuning using random/gridded search.

The dataset used is a very simple house price data in Seattle. The label is the house price in $1000, and there are 8 housing attributes and the coordinates of the house. The problem is to predict house price based on the given features.

Install sklearn if you haven't. 
https://scikit-learn.org/stable/install.html

In [1]:
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeRegressor
from sklearn.metrics import mean_squared_error, r2_score
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

In [2]:
houses = pd.read_csv("https://raw.githubusercontent.com/Ziqi-Li/GIS5122/main/data/seattle_data_cleaned.csv")

In [3]:
houses.head()

Unnamed: 0  bathrooms  sqft_living  sqft_lot  grade  condition  waterfront  \
0        9172       3.00         2660      4600      8          3           0   
1        2264       2.25         2530      8736      7          4           0   
2         348       2.00         1390     13464      7          4           0   
3       16463       1.00          940      4264      7          5           0   
4       12598       2.25         2070      7225      8          3           0   

   view  age          UTM_X         UTM_Y  log_10_price  
0     0  109  552217.557035  5.274945e+06      6.091315  
1     0   57  565692.484331  5.272758e+06      5.790988  
2     0   28  562451.661509  5.245291e+06      5.315130  
3     0   66  546816.935618  5.264407e+06      5.619093  
4     0   36  564343.195352  5.244978e+06      5.477121

In [4]:
sampled = houses.sample(frac=0.2,random_state=1)

y = 10**sampled.log_10_price/1000

X = sampled[['bathrooms','view']]

We can split the data into training (80%) and testing (20%). The model will be trained based on the training data and the testing data will be used to evaluate the model accuracy.

In [5]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

### Decision Tree 1 (max_depth=3)

Let us first try a tree with max_depth of 3

In [6]:
# Initialize the Decision Tree Regressor
dt1 = DecisionTreeRegressor(random_state=42,max_depth=3,criterion="squared_error")
dt1.fit(X_train, y_train)

DecisionTreeRegressor(max_depth=3, random_state=42)

In [7]:
# Make predictions on the testing set
y_pred = dt1.predict(X_test)

# Evaluate the model
mse = mean_squared_error(y_test, y_pred)
r2 = r2_score(y_test, y_pred)

print("Mean Squared Error:", mse)
print("R2", r2)

Mean Squared Error: 74531.32318651129
R2 0.3236760773209516


### Here I use a package which is called `dtreeviz` to visualize the tree structure.

For installation of `dtreeviz`, please see here: https://github.com/parrt/dtreeviz

The vertical line marks the split at a node, and the horizonal line marks the average value of (y) after the split.

In [8]:
import dtreeviz

viz = dtreeviz.model(dt1, X, y,
                target_name="price",
                feature_names=X.columns)

viz.view()

/Users/ziqili/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but DecisionTreeRegressor was fitted with feature names


From the decision tree it is noticable that having more bathrooms and better view will result in a higher property price.

### Decision Tree 2 (max_depth=4,min_samples_leaf=10 )

Let us tree a deeper tree

In [9]:
dt2 = DecisionTreeRegressor(random_state=42,max_depth=4,min_samples_leaf=10)
dt2.fit(X_train, y_train)

# Make predictions on the testing set
y_pred = dt2.predict(X_test)

# Evaluate the model
mse = mean_squared_error(y_test, y_pred)
r2 = r2_score(y_test, y_pred)
print("Mean Squared Error:", mse)
print("R2", r2)


Mean Squared Error: 72835.40821877561
R2 0.3390654171913684


In [10]:
viz = dtreeviz.model(dt2, X, y,
                target_name="price",
                feature_names=X.columns)
viz.view()

/Users/ziqili/anaconda3/lib/python3.11/site-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but DecisionTreeRegressor was fitted with feature names


### Using a gridded or random search method to find the optimal hyperparameters

In [11]:
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV

A grid search will try all the possible combinations of the hyperparameters you define in the grid. This might get overly slow if you have many hyperparameters and allow fine intervals.

Both search methods will involve a cross-validation, a common choice is to use `cv=5` which indicates a 5-fold cross validation.

In [12]:
# Define hyperparameter grid
param_grid = {
    
    'max_depth': [2, 4, 8, 16],
    'min_samples_split': [10, 20, 30],
    'min_samples_leaf': [10, 30, 50]
}

# Grid search
grid_search = GridSearchCV(dt1, param_grid, cv=5)
grid_search.fit(X, y)

# Best parameters and score
print("Best parameters:", grid_search.best_params_)
print("Best score:", grid_search.best_score_) #The default score is R2

Best parameters: {'max_depth': 4, 'min_samples_leaf': 10, 'min_samples_split': 30}
Best score: 0.3644613215335333


You can then use the best model to make prediction

In [13]:
best_dt = grid_search.best_estimator_
best_dt

DecisionTreeRegressor(max_depth=4, min_samples_leaf=10, min_samples_split=30,
                      random_state=42)

Similarly, this is a random search approach. Random search might be more efficient when your hyperparameter space is too large to allow a exhausive search. Here you can define the number of evaluations `n_iter=10` to limit the computation.

In [14]:
# Random search
random_search = RandomizedSearchCV(dt1, param_distributions=param_grid, n_iter=10, cv=5)
random_search.fit(X, y)

# Best parameters and score
print("Best parameters:", random_search.best_params_)
print("Best score:", random_search.best_score_) #The default score is R2

Best parameters: {'min_samples_split': 30, 'min_samples_leaf': 10, 'max_depth': 16}
Best score: 0.3640503743830714


Now, we expand the example to use all the features and try to train a best model.

In [15]:
X_all = sampled[['bathrooms', 'sqft_living', 'sqft_lot', 'grade',
       'condition', 'waterfront', 'view', 'age', 'UTM_X', 'UTM_Y']]

In [16]:
dt_all = DecisionTreeRegressor(random_state=42)

In [17]:
grid_search_all = GridSearchCV(dt_all, param_grid, cv=5)
grid_search_all.fit(X_all, y)

GridSearchCV(cv=5, estimator=DecisionTreeRegressor(random_state=42),
             param_grid={'max_depth': [2, 4, 8, 16],
                         'min_samples_leaf': [10, 30, 50],
                         'min_samples_split': [10, 20, 30]})

In [18]:
# Best parameters and score
print("Best parameters:", grid_search_all.best_params_)
print("Best score:", grid_search_all.best_score_) #The default score is R2

Best parameters: {'max_depth': 16, 'min_samples_leaf': 10, 'min_samples_split': 10}
Best score: 0.7435736171578844


The new model has a much better R2 of 0.743